**import all the essential libraries**

In [51]:
import pandas as pd
import geopandas as gpd
from sklearn.cluster import KMeans
import folium
from folium.plugins import MarkerCluster


**Load the data into a DataFrame**


In [52]:
data = pd.read_csv('/content/ev_final.csv')

# Display the first few rows to understand the structure
print(data.head())

        uid                    name             vendor_name  \
0  STATIC12  GensolCharge Pvt. Ltd.  GensolCharge Pvt. Ltd.   
1  STATIC14                    REIL                    REIL   
2  STATIC15                    REIL                    REIL   
3  STATIC16                    REIL                    REIL   
4  STATIC17                BluSmart                BluSmart   

                                      address   latitude  longitude   city  \
0             NDSE Grid, BRPL South Extension  28.568238  77.219666  Delhi   
1                       Scada office kalka ji  28.541995  77.260583  Delhi   
2                   Ashram Chowk Mathura Road  28.571189  77.259806  Delhi   
3                  Nizamuddin Railway station  28.588991  77.253240  Delhi   
4  BSES Bhawan, Nehru Place, New Delhi 110048  28.549427  77.254636  Delhi   

  country      open     close  ... postal_code           zone   0 available  \
0   India  00:00:00  23:59:59  ...      110001  central-delhi NaN       N

**Drop  any rows with missing values in crucial columns like latitude and longitude**

In [53]:
data.dropna(subset=['latitude', 'longitude'], inplace=True)

**Convert to GeoDataFrame if needed**

In [54]:
geometry = [Point(xy) for xy in zip(data['longitude'], data['latitude'])]
geo_df = gpd.GeoDataFrame(data, geometry=geometry)

**Extract the necessary columns**

In [55]:
X = data[['latitude', 'longitude']]

** Apply KMeans clustering**

In [56]:
kmeans = KMeans(n_clusters=10, random_state=42)
kmeans.fit(X)
data['cluster'] = kmeans.labels_

# Find cluster centers
cluster_centers = kmeans.cluster_centers_

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


** Convert cluster centers to GeoDataFrame for mapping **

In [57]:
cluster_centers_df = pd.DataFrame(cluster_centers, columns=['latitude', 'longitude'])
geometry_centers = [Point(xy) for xy in zip(cluster_centers_df['longitude'], cluster_centers_df['latitude'])]
geo_centers_df = gpd.GeoDataFrame(cluster_centers_df, geometry=geometry_centers)

**In Initialize the map centered on India**

In [50]:
m = folium.Map(location=[20.5937, 78.9629], zoom_start=4)

** Add charging station locations to the map & Add cluster centers to the map**

In [58]:
#add charging stations
marker_cluster = MarkerCluster().add_to(m)
for idx, row in data.iterrows():
    folium.Marker(location=[row['latitude'], row['longitude']],
                  popup=row['vendor_name'],
                  icon=folium.Icon(color='blue')).add_to(marker_cluster)
#add cluster
for idx, row in cluster_centers_df.iterrows():
    folium.Marker(location=[row['latitude'], row['longitude']],
                  popup=f'Cluster {idx}',
                  icon=folium.Icon(color='red')).add_to(m)


**save the map to an HTML file & then display the map**

In [59]:
# Save
m.save('charging_stations_map.html')

# Display
m